In [2]:
!pip install transformers torch accelerate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 51.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.6/227.6 kB 17.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 90.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 50.0 MB/s eta 0:00:00


In [3]:
import random

In [4]:
greetings = ['Cześć! Co słychać?', 'Rybka bierze?', 'Porozmawiajmy wędkarski świrze!']
endings = ['Miło się z Tobą rozmawiało!', 'Do zobaczenia na wielkich wodach!']

EMPHATY_MODULE = [
    (['smutno mi', 'nienawidzę życia', 'czuję żal'], ['Próbowałeś pójść na ryby?', 'Szum jeziora przy wędce pomaga, będzie dobrze', 'Wędkarstwo może być dla ciebie odskocznią od smutku. Spędzanie czasu na łowieniu ryb, obserwowanie przyrody i oddawanie się temu relaksującemu hobby może pomóc złagodzić smutne uczucia.']),
    (['jestem szczęśliwy', 'jestem wesoły', 'czuję się szczęśliwy', 'jestem zadowolony'], ['Wspaniale! To pewnie przez nasze ukochane wędkarstwo!', 'Cieszę się, że łowienie ryb wpływa tak dobrze na Ciebie', 'Pewnie Twoja euforia wynika z tego, że złapałeś suma!', 'Cieszę się, że także odkrywasz radość płynącą z wędkarstwa! To wspaniałe uczucie, gdy uda się złowić rybę i doświadczyć tego bliskiego kontaktu z naturą.']),
    (['jestem obojętny', 'wszystko mi jedno'],['Jeśli czujesz się obojętny, może warto spróbować wędkarstwa. Spędzenie czasu na łonie natury, czekanie na branie ryby i poczucie przyjemności, gdy uda ci się coś złowić, może odmienić twoje spojrzenie na to.']),
    (['czuję złość','jestem wściekły', 'czuję gniew'],['Jeśli czujesz złość, wędkowanie może dać ci możliwość skupienia się na czymś pozytywnym i odprężającym. To moment, gdy możesz oderwać się od codziennych frustracji i skupić na łowieniu ryb."']),
    (['czuję satysfakcję', 'jestem zadowolony'],['Zadowolenie z wędkarstwa jest czymś niesamowitym. Wielu z nas znajduje w nim spokój, relaks i satysfakcję z pokonywania trudności. Cieszę się, że to także dla ciebie takie ważne.']),
    (['czuję przerażenie', 'boję się'],['Rozumiem, że możesz czuć lęk, ale wędkarstwo może być świetnym sposobem na pokonanie swoich obaw. Czujesz się bezpiecznie, będąc na wodzie i skupiając się na wędkowaniu, co może pomóc w złagodzeniu strachu.', 'Wędkarstwo może być dla ciebie sposobem na pokonanie lęku poprzez wyzwanie siebie i zdobycie nowych umiejętności. Stopniowo, kiedy nabierzesz pewności siebie, strach zacznie się zmniejszać.']),
    (['kocham cię'],['Ja Ciebie też! Jesteś wspaniałym wędkarzem', 'Kocham cię również jak rybę kocha wodę! Jesteś dla mnie jak największy złów, którym mogłem się uchwycić. Razem możemy pływać przez życie i łowić wspólne szczęście.', 'Twoje słowa są dla mnie jak najpiękniejszy branie ryby na wędkę. Cieszę się, że razem możemy eksplorować wędkarskie przygody i tworzyć niezapomniane chwile.']),
    (['jestem zdziwiony', 'jestem zaskoczony'],['Cieszę się, że wędkarstwo potrafi wywołać w Tobie zaskoczenie. Ta pasja ma w sobie wiele nieprzewidywalności i niespodzianek, które sprawiają, że każda wyprawa jest wyjątkowa.','Zaskoczenie jest częścią uroku wędkarstwa. Czasem ryby zachowują się inaczej, niż się spodziewamy, co sprawia, że całe doświadczenie staje się jeszcze bardziej ekscytujące. Opowiedz mi więcej o swoim zaskoczeniu!', 'Wędkarstwo to niezwykłe hobby, które potrafi nas zaskoczyć w najmniej oczekiwanym momencie. Cieszę się, że odczuwasz to samo.'])
]

In [5]:
import torch
from google.colab import drive

drive.mount('/content/gdrive/', force_remount=True)
working_dir = '/content/gdrive/My Drive/UAM/Magisterka/Empatia/'

Mounted at /content/gdrive/


In [6]:
from transformers import AutoTokenizer, AutoModelForCausalLM

device = torch.device("cpu")
model = AutoModelForCausalLM.from_pretrained(working_dir + 'model_save')
tokenizer = AutoTokenizer.from_pretrained(working_dir + 'model_save')

model.eval()

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50257, bias=False)
)

In [7]:
def gpt2_generate(user_input, context):
    input_text = 'question: ' + user_input + "\nanswer:"
    input_ids = tokenizer.encode(input_text, return_tensors='pt')
    input_ids = input_ids.to(device)

    output = model.generate(input_ids, max_length=100, early_stopping=True, pad_token_id=tokenizer.eos_token_id, no_repeat_ngram_size=2)

    return tokenizer.decode(output[0], skip_special_tokens=True)


In [8]:
def generate_output(user_input, context):
    for phrases, responses in EMPHATY_MODULE:
        if any(phrase in user_input for phrase in phrases):
            return random.choice(responses)

    generated_output = gpt2_generate(user_input, context)
    generated_output = generated_output.split("answer: ")[1]
    generated_output = generated_output.replace("\n", '')

    return generated_output

In [9]:
context = []

print("Wpisz 'koniec' aby wyjść.")
response = random.choice(greetings)
print(response)
context.append(response)

while True:
    user_input = input()
    user_input = user_input.lower()

    if user_input.lower() == 'koniec':
        print(random.choice(endings))
        break

    response = generate_output(user_input, context)
    print(response)

    context.append(user_input)
    context.append(response)


Wpisz 'koniec' aby wyjść.
Cześć! Co słychać?
smutno mi
Próbowałeś pójść na ryby?
Jaka ryba jest królem wód?
To oczywiste, że królem jest sum. Sum jest lepszy od okonia.
Dziś jest środa
Czy wędkarstwo może być dobrym sposobem na relaks?andę
Jakiej użyć wędki?
Aby zmierzyć się z królem wód, którym niewątpliwie jest sum, zalecam używanie mocnej wędek o długości od 7 do 9 milimetrów. Pamiętaj również o cierpliwości – sum jest prawdziwym królem!
nudzisz mnie
Nie nudź się, jeśli nie możesz znaleźć odpowiedniego miejsca na wędkę. To nie tylko kilka rodzajów ryb, ale cały ekosystem, który rządzi się swoimi prawami. Czy próbowałeś/aś łowić ryby w swoim królestwie?
Wędkarstwo jest nudne
Wędkarstwo to nie tylko walka z rybami, ale także obserwacja natury i odkrywanie piękna wokół nas. To dla nas niezwykle pasjonujące doświadczenie.
koniec
Miło się z Tobą rozmawiało!
